# COVID-19 Data Analysis

In [1]:
import ipywidgets as widgets
from IPython.display import display, HTML

javascript_functions = {False: "hide()", True: "show()"}
button_descriptions  = {False: "Show code", True: "Hide code"}


def toggle_code(state):

    """
    Toggles the JavaScript show()/hide() function on the div.input element.
    """

    output_string = "<script>$(\"div.input\").{}</script>"
    output_args   = (javascript_functions[state],)
    output        = output_string.format(*output_args)

    display(HTML(output))


def button_action(value):

    """
    Calls the toggle_code function and updates the button description.
    """

    state = value.new

    toggle_code(state)

    value.owner.description = button_descriptions[state]


state = False
toggle_code(state)

button = widgets.ToggleButton(state, description = button_descriptions[state])
button.observe(button_action, "value")

display(button)

ToggleButton(value=False, description='Show code')

## Import Libraries

In [2]:
# Data Manipulation
import pandas as pd 
import numpy as np
import math
from datetime import timedelta

In [3]:
# Data Visualization
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from plotly.offline import plot, iplot, init_notebook_mode
init_notebook_mode(connected=True)

# import plotly.figure_factory as ff
# import matplotlib.pyplot as plt
# import seaborn as sns

# Maps
import folium

In [4]:
# Hide warnings
import warnings
warnings.filterwarnings('ignore')

In [57]:
# Define palette of colors 
red = '#ff4d4d'
green = '#64e764'
blue = '#3eb0f7'
yellow = '#f1c900'
yellowGreen ='#ddf100'
purple = '#cc00cc'
greenBlue = '#0eb194'
lightGrey = '#b0b0b0'
pink = '#ff748c'
black = '#262626'

## Exploratory Data Analysis (EDA)

### Load Covid-19 Dataset 

In [26]:
# Import fact_country Dataset
df = pd.read_csv('C:/Users/m.rachidi/Desktop/Tableau_Country.csv', sep=';', parse_dates=['Date'], encoding='latin-1')
df.head()

PK_Country      Country Country_code       Date  Confirmed  Recovered  \
0           1  Afghanistan           AF 2020-01-22          0          0   
1           2  Afghanistan           AF 2020-01-23          0          0   
2           3  Afghanistan           AF 2020-01-24          0          0   
3           4  Afghanistan           AF 2020-01-25          0          0   
4           5  Afghanistan           AF 2020-01-26          0          0   

   Deaths  Active  New_Confirmed  Last_7Days  New_Recovered  New_Deaths  \
0       0       0              0           0              0           0   
1       0       0              0           0              0           0   
2       0       0              0           0              0           0   
3       0       0              0           0              0           0   
4       0       0              0           0              0           0   

  Death_Rate  New_Active   FK_Date  FK_Rest_Country  
0          0           0  20200122                1  
1          0           0  20200123                1  
2          0           0  20200124                1  
3          0           0  20200125                1  
4          0           0  20200126                1

### Data Preprocessing 

#### Missing values and replacements

In [27]:
# Check missing values
df.isna().sum()

# Display missing values only
missing = df[df.isnull().any(axis=1)]
missing

# Country code for Namibia is missing --> fill the value
df["Country_code"].fillna("NA", inplace = True)
missing

# Check missing values
df.isna().sum()

PK_Country         0
Country            0
Country_code       0
Date               0
Confirmed          0
Recovered          0
Deaths             0
Active             0
New_Confirmed      0
Last_7Days         0
New_Recovered      0
New_Deaths         0
Death_Rate         0
New_Active         0
FK_Date            0
FK_Rest_Country    0
dtype: int64

In [28]:
# Replace country values to meet ISO denomination
replace_values = {'Bolivia':'Bolivia (Plurinational State of)','Cape Verde':'Cabo Verde',
                  'Congo (Brazzaville)':'Congo','Congo (Kinshasa)':'Congo (Democratic Republic of the)',
                  'Holy See (Vatican City State)':'Holy See','Iran, Islamic Republic of':'Iran (Islamic Republic of)',
                  'Korea (South)':'Korea (Republic of)','Lao PDR':'Lao People\'s Democratic Republic',
                  'Macedonia, Republic of':'Macedonia (the former Yugoslav Republic of)','Moldova':'Moldova (Republic of)',
                  'Palestinian Territory':'Palestine, State of','Saint Vincent and Grenadines':'Saint Vincent and the Grenadines',
                  'Syrian Arab Republic (Syria)':'Syrian Arab Republic','Taiwan, Republic of China':'Taiwan', 
                  'United Kingdom':'United Kingdom of Great Britain and Northern Ireland',
                  'Venezuela (Bolivarian Republic)':'Venezuela (Bolivarian Republic of)'}

df['Country'] = df['Country'].replace(replace_values)

# df[df['Country'] == 'Bolivia (Plurinational State of)']

# Drop useless columuns
df = df.drop(columns=['PK_Country','FK_Date', 'FK_Rest_Country'])

#### From cumulative to daily cases (Difference)

In [29]:
# Get New_Confirmed, New_Recovered, New_deaths columns using Pandas
df_group = df.groupby(['Country', 'Date'])['Confirmed', 'Recovered', 'Deaths'].sum().reset_index()
temp_group = df.groupby(['Country', 'Date'])['Confirmed', 'Recovered', 'Deaths'].sum().diff().reset_index()

# Filter and Replace data where previous country != current country
mask = temp_group['Country'] != temp_group['Country'].shift(1) # IF current country not equal to the previous country --> THEN mask = True
temp_group.loc[mask, 'Confirmed'] = np.nan
temp_group.loc[mask, 'Recovered'] = np.nan
temp_group.loc[mask, 'Deaths'] = np.nan

# Rename columuns and Merge cumulative and new data
temp_group.columns = ['Country','Date','New_Confirmed','New_Recovered','New_deaths']
df_merged = pd.merge(df_group, temp_group, on=['Country', 'Date'])
df_merged = df_merged.fillna(0)

# Change columuns datatypes
columns = ['New_Confirmed','New_Recovered','New_deaths']
df_merged[columns] = df_merged[columns].astype('int')
df_merged['New_Confirmed'] = df_merged['New_Confirmed'].apply(lambda x: 0 if x<0 else x)

# df_merged.head()

#### Aggregation on country level

In [33]:
# Total by Country
df_lastDate = df[df['Date'] == max(df['Date'])].reset_index(drop=True).drop('Date', axis=1)
df_country = df_lastDate[['Country','Confirmed','Recovered','Deaths','Active','New_Confirmed']]

# Per 100 Cases
df_country['Deaths_per_100'] = round(df_country['Deaths']/df_country['Confirmed']*100, 2)
df_country['Recovered_per_100'] = round(df_country['Recovered']/df_country['Confirmed']*100, 2)
columns = ['Deaths_per_100','Recovered_per_100']
df_country[columns] = df_country[columns].fillna(0)

df_country.head()

Country  Confirmed  Recovered  Deaths  Active  New_Confirmed  \
0  Afghanistan       1351        188      43    1120             72   
1      Albania        678        394      27     257             15   
2      Algeria       3127       1408     415    1304            120   
3      Andorra        731        344      40     347              8   
4       Angola         25          6       2      17              0   

   Deaths_per_100  Recovered_per_100  
0            3.18              13.92  
1            3.98              58.11  
2           13.27              45.03  
3            5.47              47.06  
4            8.00              24.00

### Data Enrichement 

#### Rest Countries Dataset

In [40]:
# Import RestCountries Dataset
rest_country = pd.read_excel('C:/Users/m.rachidi/Desktop/Tableau_RestCountry.xls')

# Get desired columns and rename them
rest_countries = rest_country[['Name','Alpha_2_Code','Region','Population','Latitude','Longitude']]
rest_countries.columns = ['Country','Country_Code','Region', 'Population','Latitude','Longitude']

rest_countries.head()

Country Country_Code   Region  Population   Latitude  Longitude
0     Afghanistan           AF     Asia    27657145  33.000000       65.0
1   Åland Islands           AX   Europe       28875  60.116667       19.9
2         Albania           AL   Europe     2886026  41.000000       20.0
3         Algeria           DZ   Africa    40400000  28.000000        3.0
4  American Samoa           AS  Oceania       57100 -14.333333     -170.0

#### Join tables

In [41]:
# Merge tables
df_country = pd.merge(df_country, rest_countries, on='Country', how='left')

# Cases per Population
df_country['Cases_per_M'] = round(df_country['Confirmed']/df_country['Population']*1000000)

df_country.head()

Country  Confirmed  Recovered  Deaths  Active  New_Confirmed  \
0  Afghanistan       1351        188      43    1120             72   
1      Albania        678        394      27     257             15   
2      Algeria       3127       1408     415    1304            120   
3      Andorra        731        344      40     347              8   
4       Angola         25          6       2      17              0   

   Deaths_per_100  Recovered_per_100 Country_Code  Region  Population  \
0            3.18              13.92           AF    Asia    27657145   
1            3.98              58.11           AL  Europe     2886026   
2           13.27              45.03           DZ  Africa    40400000   
3            5.47              47.06           AD  Europe       78014   
4            8.00              24.00           AO  Africa    25868000   

   Latitude  Longitude  
0      33.0       65.0  
1      41.0       20.0  
2      28.0        3.0  
3      42.5        1.5  
4     -12.5       18.5

### Data Visualization  

#### Overview of COVID-19 over time

In [42]:
# Get Data grouped by Date
temp = df_merged.groupby('Date')['Confirmed','Recovered','Deaths'].sum().reset_index()
# temp.head()

# Rename longest country names in all DataFrames
replace_values = {'United States of America':'U.S', 'United Kingdom of Great Britain and Northern Ireland':'U.K', 
                  'Iran (Islamic Republic of)':'Iran','Russian Federation':'Russia'}

df_merged['Country'] = df_merged['Country'].replace(replace_values)
df_country['Country'] = df_country['Country'].replace(replace_values)
df['Country'] = df['Country'].replace(replace_values)

In [43]:
# Plot
fig = make_subplots(rows=2, cols=2,
                    specs=[[{}, {"rowspan":2}],
                           [{}, None]],
                    subplot_titles=['Recovered','Confirmed','Deaths'])

fig.add_trace(
    go.Scatter(x=temp["Date"], y=temp["Confirmed"], name='Confirmed', marker_color=blue,
               mode='lines+markers', marker_line_width=2, marker_size=10, marker_line_color='rgb(0,134,179)'),
    row=1, col=2
)

fig.append_trace(
    go.Scatter(x=temp["Date"], y=temp["Recovered"], name='Recovered', marker_color=green,
               mode='lines+markers', marker_line_width=2, marker_size=8, marker_line_color='rgb(0,179,0)'),
    row=1, col=1
)

fig.append_trace(
    go.Scatter(x=temp["Date"], y=temp["Deaths"], name='Deaths', marker_color=pink, 
               mode='lines+markers', marker_line_width=2, marker_size=8, marker_line_color='rgba(152,0,0,.8)'),
    row=2, col=1
)

fig.update_layout(height=600, title='Cases Over Time', showlegend=False)
fig.show()

In [44]:
# Unpivot Confirmed, Recovered, Deaths --> Status to display stacked area chart
temp_unpivot = temp.melt(id_vars="Date", value_vars=[ 'Deaths','Recovered','Confirmed'], var_name='Status', value_name='Count')
# temp.head()

In [45]:
fig = px.area(temp_unpivot, x="Date", y="Count", color="Status", height=600,
             title='Stacked Cases Over Time',  color_discrete_sequence=[red,green,blue])
fig.update_layout(xaxis_rangeslider_visible=True)
fig.show()

#### COVID-19 around the world (Maps)

In [49]:
world_map = folium.Map(location=[0, 0], tiles='cartodbpositron', min_zoom=1, max_zoom=4, zoom_start=2)

for i in range(0, len(df_country)):
    folium.Circle(location=[df_country.iloc[i]['Latitude'], df_country.iloc[i]['Longitude']],
                  radius=int(df_country.iloc[i]['Confirmed'])**1.05,
                  tooltip=    '<li>Country : ' + str(df_country.iloc[i]['Country']) +
                              '<li>Confirmed : ' + str(df_country.iloc[i]['Confirmed']) +
                              '<li><bold>Deaths : ' + str(df_country.iloc[i]['Deaths']),
                  color=pink, fill=pink
                 ).add_to(world_map)


world_map

In [50]:
fig = px.choropleth(df, locations="Country", locationmode='country names', color=np.log(df["Confirmed"]),
                     hover_name="Country", animation_frame=df["Date"].dt.strftime('%Y-%m-%d'), scope='world',
                     title= 'Evolution of Confirmed Cases', color_continuous_scale=px.colors.sequential.RdPu,
                     projection='natural earth')

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "darkgrey")
fig.update_layout(coloraxis_showscale=False)
fig.show()

In [51]:
fig = px.scatter_geo(df_country, locations="Country", locationmode='country names', size=np.log(df_country["Confirmed"]), 
                     color="Region", hover_name="Country", hover_data=['Confirmed'], title= 'Confirmed Cases by Region',
                     projection='natural earth')

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "darkgrey")
fig.update_layout(coloraxis_showscale=False)
fig.show()

In [162]:
fig = px.scatter_geo(df_country, locations="Country", locationmode='country names', size=(np.log(df_country["Confirmed"]))**1.8, 
                     color=np.log(df_country["Confirmed"]), color_continuous_scale=['#e1ff2f','#c1e200','#0067cd','#400080'], 
                     hover_name="Country", hover_data=['Confirmed','Deaths'], projection = 'orthographic', 
                     title= 'Confirmed Cases around the World')

fig.update_traces(marker_line_color='#004181')
fig.update_geos(countrycolor = "white", landcolor = "white", coastlinecolor = "black",
                showocean=True, oceancolor="#23a1ae")
fig.update_layout(coloraxis_showscale=False, height=600)
fig.show()

In [70]:
fig = px.scatter_geo(df_country, locations="Country", locationmode='country names', size=(np.log(df_country["Deaths"]))**2.5, 
                     color="Deaths", color_continuous_scale=px.colors.sequential.Plasma, projection='natural earth',
                     hover_name="Country", hover_data=['Confirmed','Deaths'], title= 'Confirmed Deaths around the World')

fig.update_traces(marker_line_color='white')
fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "darkgrey")
fig.update_layout(coloraxis_showscale=False)
fig.show()

In [67]:
fig = px.scatter_geo(df_country, locations='Country', locationmode='country names', 
                     size=(np.log(df_country['Confirmed']))**2, color=np.log(df_country['Cases_per_M']), 
                     hover_name='Country', hover_data=['Cases_per_M','Confirmed'], projection = 'orthographic',
                     color_continuous_scale=px.colors.sequential.Plasma, title= 'Confirmed Cases per Million Population')

fig.update_traces(marker_line_color='purple')
fig.update_geos(landcolor = "black", coastlinecolor = "white", showocean=True, oceancolor=black )
fig.update_layout(coloraxis_showscale=False, height=600)
fig.show()

#### COVID-19 in United States

In [71]:
df_us = pd.read_csv('C:/Users/m.rachidi/Desktop/Tableau_County.csv', parse_dates=['Date'])

df_us_byDate = df_us.groupby(['Province','Code','Date'])['Confirmed','Recovered','Deaths'].sum().reset_index()

df_us_byProvince = df_us.groupby(['Province','Code'])['New_Confirmed','New_Recovered','New_Deaths'].sum().reset_index()

df_us_byCounty = df_us.groupby(['Province','Code', 'County'])['New_Confirmed','New_Recovered','New_Deaths'].sum().reset_index()

In [72]:
fig = px.choropleth(df_us_byDate, locations="Code", locationmode="USA-states", color=np.log(df_us_byDate["Confirmed"]),
                    hover_name="Province", scope='usa', animation_frame=df_us_byDate["Date"].dt.strftime('%Y-%m-%d'),
                    title= 'Evolution of Confirmed Cases Over Time', color_continuous_scale=px.colors.sequential.Greens)

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "white")
fig.update_layout(coloraxis_showscale=False)
fig.show()

In [73]:
fig = px.choropleth(df_us_byProvince, locations='Code', locationmode='USA-states', scope='usa',
                     color=np.log(df_us_byProvince['New_Confirmed']), hover_name='Province', hover_data=['New_Confirmed'],
                     color_continuous_scale=px.colors.sequential.ice_r, title= 'Confirmed Cases by State')

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "white")
fig.update_layout(coloraxis_showscale=False)
fig.show()

In [74]:
df_geo = pd.read_csv('C:/Users/m.rachidi/Desktop/Tableau_Geo.csv', sep=';', encoding='latin-1')

# Replace commas with points in latitude and longitude 
df_geo['Lat'] = df_geo['Lat'].str.replace(',','.')
df_geo['Lon'] = df_geo['Lon'].str.replace(',','.')

# Convert now the columns to float
df_geo[['Lat']] = df_geo[['Lat']].astype(float)
df_geo[['Lon']] = df_geo[['Lon']].astype(float)

# Get data for US
df_us_geo = df_geo[df_geo['Country_Code'] == 'US']
df_us_geo.head()

# Clean missing values for US: province, city and city code
df_us_geo['Province'] = df_us_geo['Province'].fillna('Unknown')
df_us_geo['City'] = df_us_geo['City'].fillna('Unassigned')
df_us_geo['City_Code'] = df_us_geo['City_Code'].fillna(0.0)

# Check remaining missing values
null = df_us_geo[df_us_geo.isnull().any(axis=1)]
null

# Remove country columns
df_us_geo = df_us_geo.drop(columns=['Country','Country_Code'])

# Group by County 
df_us_geo = df_us_geo.groupby(['Province','City','Lat','Lon','City_Code']).sum().reset_index()

# Remove unassigned location from dataframe
df_us_geo = df_us_geo[df_us_geo['City']!='Unassigned']
df_us_geo = df_us_geo[df_us_geo['Lat']!= 0.0]

df_us_geo.sort_values(['Province','City'])

Province        City    Lat     Lon  City_Code
0     Alabama     Autauga  32.54  -86.64     1001.0
1     Alabama     Baldwin  30.73  -87.72     1003.0
2     Alabama     Barbour  31.87  -85.39     1005.0
3     Alabama        Bibb  33.00  -87.13     1007.0
4     Alabama      Blount  33.98  -86.57     1009.0
...       ...         ...    ...     ...        ...
3247  Wyoming  Sweetwater  41.66 -108.88    56037.0
3248  Wyoming       Teton  43.94 -110.59    56039.0
3249  Wyoming       Uinta  41.29 -110.55    56041.0
3251  Wyoming    Washakie  43.90 -107.68    56043.0
3252  Wyoming      Weston  43.84 -104.57    56045.0

[3143 rows x 5 columns]

In [75]:
# Rename columns for join
df_us_geo = df_us_geo.rename(columns={'City':'County','Lat':'Latitude','Lon':'Longitude'})
 
# Remove unassigned location from dataframe
df_us_byCounty = df_us_byCounty[df_us_byCounty['County']!='Unassigned']
df_us_byCounty = df_us_byCounty[~df_us_byCounty['County'].str.contains('Out of')]

# Join data to df_us_byCounty
df_us_byCounty = pd.merge(df_us_byCounty, df_us_geo, on=['Province','County'], how='left')
df_us_byCounty = df_us_byCounty.rename(columns={'New_Confirmed':'Confirmed Cases','New_Deaths':'Confirmed Deaths'})
df_us_byCounty

Province Code      County  Confirmed Cases  New_Recovered  \
0     Alabama   AL     Autauga               36              0   
1     Alabama   AL     Baldwin              147              0   
2     Alabama   AL     Barbour               32              0   
3     Alabama   AL        Bibb               34              0   
4     Alabama   AL      Blount               31              0   
...       ...  ...         ...              ...            ...   
3138  Wyoming   WY  Sweetwater               16              0   
3139  Wyoming   WY       Teton               95              0   
3140  Wyoming   WY       Uinta                7              0   
3141  Wyoming   WY    Washakie                8              0   
3142  Wyoming   WY      Weston                0              0   

      Confirmed Deaths  Latitude  Longitude  City_Code  
0                    2     32.54     -86.64     1001.0  
1                    3     30.73     -87.72     1003.0  
2                    0     31.87     -85.39     1005.0  
3                    0     33.00     -87.13     1007.0  
4                    0     33.98     -86.57     1009.0  
...                ...       ...        ...        ...  
3138                 0     41.66    -108.88    56037.0  
3139                 0     43.94    -110.59    56039.0  
3140                 0     41.29    -110.55    56041.0  
3141                 0     43.90    -107.68    56043.0  
3142                 0     43.84    -104.57    56045.0  

[3143 rows x 9 columns]

In [76]:
fig = px.scatter_geo(df_us_byCounty, lat='Latitude', lon='Longitude', locationmode='USA-states', scope='usa',
                     size=(np.log(df_us_byCounty["Confirmed Cases"]))**2.5, 
                     color=np.log(df_us_byCounty["Confirmed Cases"]), color_continuous_scale=px.colors.sequential.Plasma_r,
                     hover_name='County', hover_data=['Province','Code','Confirmed Cases','Confirmed Deaths'],
                     title='Confirmed Cases by City ')

fig.update_traces(marker_line_color='orange')
fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "white")
fig.update_layout(coloraxis_showscale=False, height=600)
fig.show()

#### COVID-19 in Morocco

In [77]:
#Load Morocco data with cases by Province
df_ma = pd.read_csv('C:/Users/m.rachidi/Desktop/Tableau_MA_province.csv')
df_ma = df_ma.drop(columns='Unnamed: 0', axis=1)
replace_values = {'Oriental':'Oujda Nador'}
df_ma['Province'] = df_ma['Province'].replace(replace_values)

df_ma['Id'] = np.arange(1,13)
df_ma

# Load Morocco data with latitude and longitude by City
df_ma_cities = pd.read_csv('C:/Users/m.rachidi/Desktop/Morocco_cities.txt', delimiter=',', encoding='latin-1')
df_ma_cities.head()

City   Latitude  Longitude  Id
0  Casablanca  33.588310   -7.61138   2
1       Rabat  34.013248   -6.83255  10
2         Fès  34.033131   -5.00028   5
3        Sale  34.053101   -6.79846  10
4   Marrakesh  31.634159   -7.99994   8

In [78]:
# Set main cities as reference for Province
cities_reference = ['Casablanca','Beni Mellal','Fès','Marrakesh','Oujda-Angad','Rabat','Agadir','Tanger',
                    'Dakhla','Guelmim','Errachidia','Laâyoune']
df_ma_cities = df_ma_cities[df_ma_cities['City'].isin(cities_reference)]

# Merge dataframes
df_ma = pd.merge(df_ma, df_ma_cities,on='Id', how='left')
df_ma = df_ma.drop('Id', axis=1)

df_ma

Province  Cases         City   Latitude  Longitude
0        Beni Mellal-Khénifra     78  Beni Mellal  32.337250  -6.349830
1                 Casa Settat    982   Casablanca  33.588310  -7.611380
2             Daraa-tafilalet    371   Errachidia  31.927200  -4.428500
3        Dakhla-Oued Ed Dahab      2       Dakhla  23.704895 -15.943179
4                  Fès meknes    499          Fès  34.033131  -5.000280
5           Guelmim Oued Noun      6      Guelmim  28.988400 -10.052700
6     Laâyoune-Sakia El Hamra      4     Laâyoune  27.150000 -13.199100
7              Marrakech Safi    802    Marrakesh  31.634159  -7.999940
8                 Oujda Nador    175  Oujda-Angad  34.681389  -1.908580
9          Rabat Salé Kenitra    297        Rabat  34.013248  -6.832550
10                Souss-Massa     50       Agadir  30.420179  -9.598150
11  Tanger Tetouan Al Hoceima    492       Tanger  35.767269  -5.799750

In [79]:
world_map = folium.Map(location=[35, -10], tiles='cartodbpositron', min_zoom=1, max_zoom=4, zoom_start=20)

for i in range(0, len(df_ma)):
    folium.Circle(location=[df_ma.iloc[i]['Latitude'], df_ma.iloc[i]['Longitude']],
                  radius=int(df_ma.iloc[i]['Cases'])**1.8,
                  tooltip=    '<li>Province : ' + str(df_ma.iloc[i]['Province']) +
                              '<li># Cases : ' + str(df_ma.iloc[i]['Cases']),
                  color='crimson', fill='crimson'
                 ).add_to(world_map)


world_map

In [80]:
fig = px.scatter_geo(df_ma, locationmode='country names', lat='Latitude', lon='Longitude', scope = 'africa',
                     color=np.log(df_ma["Cases"]**1.5), size=np.log(df_ma["Cases"]**1.5), hover_data=['Province','Cases'],
                     color_continuous_scale=['#a6ff4d','#d3ff4d','#89e200', red], title= 'Confirmed Cases in US')


fig.update_traces(marker_line_color='red')
fig.update_geos(fitbounds="locations", countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "white")
fig.update_layout(coloraxis_showscale=False)
fig.show()

#### Affected Countries by COVID-19

In [81]:
data = df

def function(data):
    if data['Confirmed'] == 0:
        val = 0
    else:
        val = 1
    return val

data['Affected Countries'] = data.apply(function, axis=1)
data_byDate = data.groupby('Date')['Affected Countries'].sum().reset_index()

fig = px.scatter(data_byDate, x='Date', y='Affected Countries', title='Number of countries where COVID-19 has spread')

fig.update_traces(mode='lines+markers', marker_color='rgba(255, 182, 193, .9)', marker_size=10, marker_line_width=2, 
                  marker_line_color='rgba(152, 0, 0, .8)')
fig.show()

In [83]:
# Get New Cases Data grouped by Date (frist pair of plots -- New Cases)
df_newCases = df_merged.groupby('Date')['New_Confirmed','New_Recovered','New_deaths'].sum().reset_index()

#=============================================================================================================================#

# Get Total Cases on Last Date by Country (second pair of plots -- Top 10)
df_lastDate = df[df['Date'] == max(df['Date'])].reset_index(drop=True).drop('Date', axis=1)
df_totalCases = df_lastDate[['Country','Confirmed','Recovered','Deaths','Active','New_Confirmed']]

# Sort values and get the 10 higher ones for confirmed and deaths
df_topConfirmed = df_totalCases.sort_values(by=['Confirmed']).tail(10)
df_topDeaths= df_totalCases.sort_values(by=['Deaths']).tail(10)

In [84]:
# Using temp DataFrame previously calculated 
fig = make_subplots(rows=2, cols=2, vertical_spacing=0.1, subplot_titles=['Confirmed','Deaths','Most Confirmed','Most Deaths'])

fig.add_trace(
    go.Scatter(x=temp["Date"], y=temp["Confirmed"], name='Confirmed', marker_color=blue,
           mode='lines+markers', marker_line_width=2, marker_size=10, marker_line_color='rgb(0,134,179)'),
    row=1, col=1
)

fig.add_trace(
    go.Scatter(x=temp["Date"], y=temp["Deaths"], name='Deaths', marker_color=pink,
               mode='lines+markers', marker_line_width=2, marker_size=10, marker_line_color='rgba(152,0,0,.8)'),
    row=1, col=2
)

# Using newly created DataFrame
fig.add_trace(
    go.Bar(x=df_topConfirmed["Confirmed"], y=df_topConfirmed["Country"], name="Confirmed", orientation='h', marker_color=blue),
    row=2, col=1
)

fig.add_trace(
    go.Bar(x=df_topDeaths["Deaths"], y=df_topDeaths["Country"], name="Deaths", orientation='h', marker_color=pink),
    row=2, col=2
)

fig.update_layout(height=900, title='Cases Over Time and Most Affected Countries', showlegend=False)
fig.show()

In [85]:
# Split data into China and Rest of World 
df_China = df_merged[df_merged['Country'] == 'China']
df_RestWorld = df_merged[df_merged['Country'] != 'China']

# Get New Cases Data grouped by Date 
df_China = df_China.groupby(['Date'])['New_Confirmed','New_Recovered','New_deaths'].sum().reset_index()
df_RestWorld = df_RestWorld.groupby(['Date'])['New_Confirmed','New_Recovered','New_deaths'].sum().reset_index()

In [86]:
fig = make_subplots(rows=1, cols=2,
                    subplot_titles=['Daily Confirmed in China','Daily Confirmed in Rest of the World'])

fig.add_trace(
    go.Bar(x=df_China["Date"], y=df_China["New_Confirmed"], name='China', marker_color=lightGrey),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=df_RestWorld["Date"], y=df_RestWorld["New_Confirmed"], name='Rest of World', marker_color=pink),
    row=1, col=2
)

fig.update_layout(height=500, title='China vs Rest of the World', showlegend=False)
fig.show()

In [87]:
# Sort values and get the 10 higher ones for confirmed and deaths
df_topNew_Confirmed = df_country.sort_values(by=['New_Confirmed']).tail(10)
df_topCases_M= df_country.sort_values(by=['Cases_per_M']).tail(10)
df_topDeaths_100= df_country.sort_values(by=['Deaths_per_100']).tail(10)

In [88]:
fig = make_subplots(rows=1, cols=3, horizontal_spacing=0.14,
                    subplot_titles=['New Confirmed Cases', 'Deaths / 100 Cases', 'Cases / Million People'])

fig.add_trace(
    go.Bar(x=df_topNew_Confirmed["New_Confirmed"], y=df_topNew_Confirmed["Country"], name="New Confirmed", 
           orientation='h', marker_color='coral', opacity=0.8),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=df_topDeaths_100["Deaths_per_100"], y=df_topDeaths_100["Country"], name="Deaths per 100 Cases", 
           orientation='h', marker_color=red, opacity=0.8),
    row=1, col=2
)

fig.add_trace(
    go.Bar(x=df_topCases_M["Cases_per_M"], y=df_topCases_M["Country"], name='Cases per Million',
           orientation='h', marker_color='purple', opacity=0.8),
    row=1, col=3
)

fig.update_layout(height=500, showlegend=False, title='Top 10 ...')
fig.show()

#### Analysis by Country 

In [89]:
df_topDeaths= df_country.sort_values(by=['Deaths']).tail(15)

fig = px.scatter(df_topDeaths, x="Confirmed", y="Deaths", color="Country", size="Deaths", text="Country", 
                 log_x=True, log_y=True)

fig.update_traces(textposition='top center')
fig.update_layout(height= 600,showlegend=False, title="Death - Confirmed Cases Comparison in Logarithmic Scale ")
fig.show()

##### Set Period Time to Days from Day One (100th Case)

In [101]:
# Get rows from 100 confirmed cases
cases_100 = df[df['Confirmed']>=100]

# Get the first date for each country from 100th Case
dayone = cases_100.groupby('Country')['Date'].min().reset_index()
dayone.columns = ['Country', 'DayOne']

# Merge dayone and cases_100
from_dayone = pd.merge(cases_100, dayone, on='Country')

# Calculate the difference b/w Date and DayOne to get the number of days since 100th Case
from_dayone['Days'] = (from_dayone['Date'] - from_dayone['DayOne']).dt.days

In [102]:
main_countries = ['Australia', 'Belgium', 'China', 'France', 'Germany','Iran', 'Italy', 'Japan', 
                  'Korea (Republic of)', 'Spain', 'Turkey', 'U.K', 'U.S']

mask = from_dayone[from_dayone['Country'].isin(main_countries)]

fig = px.line(mask, x="Days", y="Confirmed", color="Country", height=600, log_y=True, 
              color_discrete_sequence= px.colors.qualitative.Dark2, title='COVID-19 Confirmed Cases from 100th Case')

fig.update_traces(mode='lines', line_width=3)
fig.show()

In [103]:
fig = px.scatter(mask, x='Confirmed', y='Last_7Days', color='Country', log_x=True, log_y=True, height=600, text='Country',
              color_discrete_sequence= px.colors.qualitative.Dark2, title='Spread of Confirmed Cases from 100th Case')

fig.update_traces(mode='lines', line_width=3)
fig.show()

In [104]:
from_dayone = pd.merge(from_dayone, df_country[['Country','Region']], on='Country', how='left')

df_region = from_dayone.groupby(['Date','Region'])['Confirmed','Recovered','Deaths','Active','New_Confirmed','New_Recovered',
                                                   'New_Deaths','Last_7Days'].sum().reset_index()

In [107]:
fig = px.scatter(df_region, x="Date", y="Confirmed", color="Region", hover_name="Region", 
              color_discrete_sequence= px.colors.qualitative.Bold, height=600, title='Confirmed Cases Over Time by Region')


fig.update_traces(mode='lines', line_width=4)


fig.show()

In [108]:
mask = df_country[df_country['Country'].isin(main_countries)]
mask = mask.sort_values(by='Confirmed', ascending=False)
mask_unpivot = mask.melt(id_vars='Country', value_vars=['Confirmed','Deaths'], var_name='Status', value_name='Count')

fig = px.treemap(mask_unpivot, path=['Country','Status'], values="Count", height=600,
                 color_discrete_sequence= px.colors.qualitative.Bold, title='Classification by Confirmed Cases and Deaths' )
fig.data[0].textinfo = 'label+text+value'
fig.show()



In [109]:
main_countries = ['Belgium', 'France', 'U.K',
                  'Germany', 'Spain', 'Italy',
                  'Korea (Republic of)', 'China', 'U.S']
    
fig = make_subplots(rows=3, cols=3, subplot_titles=main_countries)
rows = [1,1,1,2,2,2,3,3,3]
cols = [1,2,3,1,2,3,1,2,3]

for row, col, country in zip(rows,cols,main_countries):
    fig.add_trace(
        go.Scatter(x=df_merged.loc[df_merged['Country']== country, 'Date'], 
                   y=df_merged.loc[df_merged['Country']== country,'Confirmed'],
                   name=country, mode='lines+markers', marker_line_width=1, marker_size=5.5),
        row=row, col=col
    )

fig.update_layout(height=800, title_text="No. of Confirmed Cases in each Country", showlegend=False)    
fig.show()

#### Trend Analysis 

In [110]:
df_date = from_dayone.groupby(['Date'])['Confirmed','Recovered','Deaths'].sum().reset_index()
df_date['Days'] = df_date['Date'].min()
df_date['Days'] = (df_date['Date'] - df_date['Days']).dt.days

fig = px.scatter(df_date, x='Days', y='Confirmed', title='World Trend of Confirmed Cases')

fig.update_traces(mode='lines+markers', marker_color=purple, marker_size=10, marker_line_width=2, 
                  marker_line_color='rgba(152, 0, 0, .8)')
fig.show()

fig = px.scatter(df_date, x='Days', y='Confirmed', log_y=True, title='World Trend of Confirmed Cases (log scale)')

fig.update_traces(mode='lines+markers', marker_color='steelblue', marker_size=10, marker_line_width=2, 
                  marker_line_color='rgba(152, 0, 0)')
fig.show()

#### Comparison with ohter epidemics

In [111]:
df_sars = pd.read_excel('C:/Users/m.rachidi/Desktop/Tableau_Epidemics.xls', sheet_name='SARS', parse_dates=['Date'])
df_h1n1 = pd.read_excel('C:/Users/m.rachidi/Desktop/Tableau_Epidemics.xls', sheet_name='H1N1', parse_dates=['Date'])
df_ebola = pd.read_excel('C:/Users/m.rachidi/Desktop/Tableau_Epidemics.xls', sheet_name='EBOLA', parse_dates=['Date'])

##### Clean Sars Data

In [112]:
# Find rows where Country contains a comma and clean the column
df_sars[df_sars['Country'].str.find(",")!= -1].sort_values('Country')
df_sars['Country'] = df_sars['Country'].str.split(',', expand=True)

# Check for missing values and fill them
null_data = df_sars[df_sars.isnull().any(axis=1)]
df_sars = df_sars.fillna(-1)

#Convert columns datatypes from string to int 
df_sars[['Cases','Deaths','Recovered']] = df_sars[['Cases','Deaths','Recovered']].astype(int)

df_sars.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2538 entries, 0 to 2537
Data columns (total 6 columns):
Disease      2538 non-null object
Country      2538 non-null object
Date         2538 non-null datetime64[ns]
Cases        2538 non-null int32
Deaths       2538 non-null int32
Recovered    2538 non-null int32
dtypes: datetime64[ns](1), int32(3), object(2)
memory usage: 89.4+ KB


##### Clean H1N1 Data

In [113]:
# Find rows where Country contains a comma: Seperate Clean and not Clean data 
# Clean
df_h1n1_clean = df_h1n1[df_h1n1['Country'].str.find(",") == -1].sort_values('Country')
df_h1n1_clean['Country'] = df_h1n1_clean['Country'].str.strip()

# Not Clean
df_toClean = df_h1n1[df_h1n1['Country'].str.find(",")!= -1].sort_values('Country')
df_toClean['Country'] = df_toClean['Country'].str.strip()

In [114]:
# Split and Clean PART 1
df_split = df_toClean['Country'].str.split(',', n=1, expand=True)

countries_ok = ['Bermuda','British Virgin Islands','Cayman Islands','Iran','Korea','French Polynesia','Martinique',
                'Guadaloupe','Guernsey','Isle of Man','Jersey','New Caledonia','Saint Martin']

df_toClean['Country1'] = df_split[0]
df_toClean['Country2'] = df_split[1]

data1 = df_toClean[df_toClean['Country1'].isin(countries_ok)]

# Split and Clean PART 2
df_split = df_toClean['Country2'].str.split(',', expand=True)

countries_ok = ['French Polynesia','Martinique','Curacao','Isle of Man','Jersey','New Caledonia','Sint Maarten','Aruba']

# Remove white spaces in country names
df_split[0] = df_split[0].str.strip()

# Replace values
replace_values = {'Curaçao':'Curacao','Curaçao *':'Curacao','Curaçao **':'Curacao'}
df_split[0] = df_split[0].replace(replace_values)

df_toClean['Country3'] = df_split[0]
df_toClean['Country4'] = df_split[1]

data2 = df_toClean[df_toClean['Country3'].isin(countries_ok)]
data2 = data2.drop(['Country1', 'Country2','Country4'], axis=1)
data2.rename(columns = {'Country3':'Country1'}, inplace=True)

In [115]:
# Concatenate cleaned data
data = pd.concat([data1,data2], axis=0)
data_cleaned = data.drop(['Country','Country2'], axis=1)
data_cleaned = data_cleaned.rename(columns={'Country1':'Country'})

# Concatenate All data
df_h1n1 = pd.concat([df_h1n1_clean, data_cleaned], axis=0)

# Replace duplicates and standardize country names
replace_values = {'Costa Rica*':'Costa Rica', 'Morocco *':'Morocco', 'The former Yugoslav Republic of Macedonia':'Macedonia', 
                  'United Kingdom':'U.K', 'UK':'U.K', 'United States of America*':'U.S', 'United States of America':'U.S',
                  'British Virgin Islands':'Virgin Islands'}
df_h1n1['Country'] = df_h1n1['Country'].replace(replace_values)

# Check for missing values and fill them
null_data = df_h1n1[df_h1n1.isnull().any(axis=1)]
df_h1n1 = df_h1n1.fillna(-1)

#Convert columns datatypes from string to int 
df_h1n1[['Cases','Deaths']] = df_h1n1[['Cases','Deaths']].astype(int)
df_h1n1.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2031 entries, 0 to 82
Data columns (total 5 columns):
Cases      2031 non-null int32
Country    2031 non-null object
Date       2031 non-null datetime64[ns]
Deaths     2031 non-null int32
Disease    2031 non-null object
dtypes: datetime64[ns](1), int32(2), object(2)
memory usage: 79.3+ KB


##### Clean Ebola Data

In [116]:
# Check for missing values and fill them
null_data = df_ebola[df_ebola.isnull().any(axis=1)]
df_ebola = df_ebola.fillna(-1)

#Convert columns datatypes from string to int 
df_ebola[['Cases','Deaths']] = df_ebola[['Cases','Deaths']].astype(int)
df_ebola.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2485 entries, 0 to 2484
Data columns (total 5 columns):
Disease    2485 non-null object
Country    2485 non-null object
Date       2485 non-null datetime64[ns]
Cases      2485 non-null int32
Deaths     2485 non-null int32
dtypes: datetime64[ns](1), int32(2), object(2)
memory usage: 77.8+ KB


##### Clean Covid Data

In [117]:
df_covid = df[['Confirmed','Country','Date','Deaths','Recovered']]
df_covid = df_covid.rename(columns={'Confirmed':'Cases'})
df_covid['Disease'] = "COVID"
df_covid.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17202 entries, 0 to 17201
Data columns (total 6 columns):
Cases        17202 non-null int64
Country      17202 non-null object
Date         17202 non-null datetime64[ns]
Deaths       17202 non-null int64
Recovered    17202 non-null int64
Disease      17202 non-null object
dtypes: datetime64[ns](1), int64(3), object(2)
memory usage: 806.5+ KB


In [118]:
# Concatenate all epidemics
df_epidemic = pd.concat([df_sars,df_h1n1,df_ebola,df_covid], axis=0)

df_group = df_epidemic.groupby(['Disease','Country','Date'])['Cases','Deaths'].sum().reset_index()
temp = df_epidemic.groupby(['Country','Date'])['Cases','Deaths'].sum().diff().reset_index()

# Filter and Replace data where previous country != current country
mask = temp['Country'] != temp['Country'].shift(1) # IF current country not equal to the previous country --> THEN mask = True
temp.loc[mask, 'Cases'] = np.nan
temp.loc[mask, 'Deaths'] = np.nan

# Rename columuns and Merge cumulative and new data
temp.columns = ['Country','Date','New Cases','New Deaths']
df_merged = pd.merge(df_group, temp, on=['Country', 'Date'])
df_merged = df_merged.fillna(0)

# Change columuns datatypes
columns = ['New Cases','New Deaths']
df_merged[columns] = df_merged[columns].astype('int')
df_merged['New Cases'] = df_merged['New Cases'].apply(lambda x: 0 if x<0 else x)
df_merged['New Deaths'] = df_merged['New Deaths'].apply(lambda x: 0 if x<0 else x)
df_merged

Disease      Country       Date  Cases  Deaths  New Cases  New Deaths
0       COVID  Afghanistan 2020-01-22      0       0          0           0
1       COVID  Afghanistan 2020-01-23      0       0          0           0
2       COVID  Afghanistan 2020-01-24      0       0          0           0
3       COVID  Afghanistan 2020-01-25      0       0          0           0
4       COVID  Afghanistan 2020-01-26      0       0          0           0
...       ...          ...        ...    ...     ...        ...         ...
24143    SARS     Viet Nam 2003-07-07     63       5          0           0
24144    SARS     Viet Nam 2003-07-08     63       5          0           0
24145    SARS     Viet Nam 2003-07-09     63       5          0           0
24146    SARS     Viet Nam 2003-07-10     63       5          0           0
24147    SARS     Viet Nam 2003-07-11     63       5          0           0

[24148 rows x 7 columns]

In [119]:
df_disease = df_merged.groupby('Disease')['New Cases', 'New Deaths'].sum().reset_index() 

## Single graph of Confirmed Cases by Disease
# fig = px.bar(df_disease, x='Disease', y='New Cases', log_y=True,
#              hover_name='Disease', labels={'New Cases':'Total Cases'}, color='Disease',
#              title='Confirmed Cases by Disease (log scale)', color_discrete_sequence=px.colors.qualitative.Bold)
# fig.show()

temp_unpivot = df_disease.melt(id_vars="Disease", value_vars=['New Cases','New Deaths'], var_name='Status', value_name='Count')

fig = px.bar(temp_unpivot, x="Disease", y="Count", facet_col="Status", log_y=True, text='Count', height=600, opacity=0.8,
             color="Disease", color_discrete_sequence=px.colors.qualitative.Bold, title='Confirmed Cases by Disease')

fig.update_traces(texttemplate='%{text:.2s}', textposition='outside')
fig.show()

#### Disease Analysis

##### SARS 

In [120]:
# Group the SARS data by date 
df_SARS = df_sars.groupby('Date')['Cases','Deaths','Recovered'].sum().reset_index()

# Get missing dates and add them to dataframe
r = pd.date_range(start=df_SARS.Date.min(), end=df_SARS.Date.max())
df_SARS = df_SARS.set_index('Date').reindex(r).rename_axis('Date').reset_index()

# Check for missing values
null_data = df_SARS[df_SARS.isnull().any(axis=1)]
null_data 

# Fill the missing values using interpolation
df_SARS['Interpolated_Cases'] =  df_SARS['Cases'].interpolate()
df_SARS['Interpolated_Deaths'] =  df_SARS['Deaths'].interpolate()
df_SARS.head()

#Convert new column datatype from string to int 
df_SARS[['Interpolated_Cases']] = df_SARS[['Interpolated_Cases']].astype(int)
df_SARS[['Interpolated_Deaths']] = df_SARS[['Interpolated_Deaths']].astype(int)
df_SARS.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 117 entries, 0 to 116
Data columns (total 6 columns):
Date                   117 non-null datetime64[ns]
Cases                  96 non-null float64
Deaths                 96 non-null float64
Recovered              96 non-null float64
Interpolated_Cases     117 non-null int32
Interpolated_Deaths    117 non-null int32
dtypes: datetime64[ns](1), float64(3), int32(2)
memory usage: 4.7 KB


In [121]:
# # Plot two charts side by side (Cases and Deaths Over Time)
# fig = make_subplots(rows=1, cols=2, 
#                     subplot_titles=['Confirmed Cases', 'Confirmed Deaths'])

# fig.add_trace(
#     go.Bar(x=df_SARS['Date'], y=df_SARS['Interpolated_Cases'], name='Confirmed Cases', marker_color=blue),
#     row=1, col=1
# )

# fig.add_trace(
#     go.Bar(x=df_SARS['Date'], y=df_SARS['Interpolated_Deaths'], name='Confirmed Deaths', marker_color=pink),
#     row=1, col=2
# )

# # fig = px.area(df_SARS, x='Date', y='Interpolated_Cases', color_discrete_sequence=[yellowGreen], 
# #               title='Confirmed SARS Cases Over Time')

# fig.update_layout(title='Confirmed SARS Cases Over Time') # xaxis_tickformat = '%B<br>%Y', xaxis = dict(tickangle = -45)
# fig.show()

# Plot stacked chart (Cases and Deaths Over Time)
# Unpivot Confirmed, Recovered, Deaths --> Status to display stacked area chart
temp_unpivot = df_SARS.melt(id_vars="Date", value_vars=[ 'Interpolated_Deaths','Interpolated_Cases'], var_name='Status', value_name='Count')

fig = px.area(temp_unpivot, x="Date", y="Count", color="Status", height=600,
             title='Stacked SARS Cases Over Time',  color_discrete_sequence=[red,blue])
fig.update_layout(xaxis_rangeslider_visible=True)
fig.show()

In [122]:
# df_sars
df_sars = df_merged[df_merged['Disease']=='SARS']
df_sars = df_sars.groupby('Country')['New Cases','New Deaths'].sum().reset_index()

fig = px.choropleth(df_sars, locations="Country", locationmode="country names", color=np.log(df_sars["New Cases"]),
                    hover_name="Country", scope='world', projection='natural earth',
                    title= 'Confirmed SARS Cases', color_continuous_scale=px.colors.sequential.RdPu)

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "darkgrey")
fig.update_layout(showlegend=False, coloraxis_showscale=False)
fig.show()


##### H1N1 

In [123]:
# Group the SARS data by date 
df_H1N1 = df_h1n1.groupby('Date')['Cases','Deaths'].sum().reset_index()

# Get missing dates and add them to dataframe
r = pd.date_range(start=df_H1N1.Date.min(), end=df_H1N1.Date.max())
df_H1N1 = df_H1N1.set_index('Date').reindex(r).rename_axis('Date').reset_index()

# Check for missing values
null_data = df_H1N1[df_H1N1.isnull().any(axis=1)]
null_data 

# Fill the missing values using interpolation
df_H1N1['Interpolated_Cases'] =  df_H1N1['Cases'].interpolate()
df_H1N1['Interpolated_Deaths'] =  df_H1N1['Deaths'].interpolate()

# Convert new column datatype from string to int 
df_H1N1[['Interpolated_Cases']] = df_H1N1[['Interpolated_Cases']].astype(int)
df_H1N1[['Interpolated_Deaths']] = df_H1N1[['Interpolated_Deaths']].astype(int)

df_H1N1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 50 entries, 0 to 49
Data columns (total 5 columns):
Date                   50 non-null datetime64[ns]
Cases                  12 non-null float64
Deaths                 12 non-null float64
Interpolated_Cases     50 non-null int32
Interpolated_Deaths    50 non-null int32
dtypes: datetime64[ns](1), float64(2), int32(2)
memory usage: 1.7 KB


In [124]:
# Plot two charts side by side (Cases and Deaths Over Time)
fig = make_subplots(rows=1, cols=2, 
                    subplot_titles=['Confirmed Cases', 'Confirmed Deaths'])

fig.add_trace(
    go.Bar(x=df_H1N1['Date'], y=df_H1N1['Interpolated_Cases'], name='Confirmed Cases', marker_color=blue),
    row=1, col=1
)

fig.add_trace(
    go.Bar(x=df_H1N1['Date'], y=df_H1N1['Interpolated_Deaths'], name='Confirmed Deaths', marker_color=pink),
    row=1, col=2
)

# fig = px.area(df_H1N1, x='Date', y='Interpolated_Cases', color_discrete_sequence=[blue], 
#               title='Confirmed H1N1 Cases Over Time')

fig.update_layout(title='Confirmed H1N1 Cases Over Time') # xaxis_tickformat = '%B<br>%Y', xaxis = dict(tickangle = -45)
fig.show()

In [125]:
# df_h1n1
df_h1n1 = df_merged[df_merged['Disease']=='H1N1']
df_h1n1 = df_h1n1.groupby('Country')['New Cases','New Deaths'].sum().reset_index()

fig = px.choropleth(df_h1n1, locations="Country", locationmode="country names", color=np.log(df_h1n1["New Cases"]),
                    hover_name="Country", scope='world', hover_data=['New Cases','New Deaths'], projection='natural earth',
                    title= 'Confirmed H1N1 Cases', color_continuous_scale=px.colors.sequential.Blues)

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "darkgrey")
fig.update_layout(showlegend=False, coloraxis_showscale=False)
fig.show()

##### Ebola 

In [126]:
# Group the SARS data by date 
df_EBOLA = df_ebola.groupby('Date')['Cases','Deaths'].sum().reset_index()

# Get missing dates and add them to dataframe
r = pd.date_range(start=df_EBOLA.Date.min(), end=df_EBOLA.Date.max())
df_EBOLA = df_EBOLA.set_index('Date').reindex(r).rename_axis('Date').reset_index()

# Check for missing values
null_data = df_EBOLA[df_EBOLA.isnull().any(axis=1)]
null_data 

# Fill the missing values using interpolation
df_EBOLA['Interpolated_Cases'] = df_EBOLA['Cases'].interpolate()
df_EBOLA['Interpolated_Deaths'] = df_EBOLA['Deaths'].interpolate()

# Convert new column datatype from string to int 
df_EBOLA[['Interpolated_Cases']] = df_EBOLA[['Interpolated_Cases']].astype(int)
df_EBOLA[['Interpolated_Deaths']] = df_EBOLA[['Interpolated_Deaths']].astype(int)

df_EBOLA.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 573 entries, 0 to 572
Data columns (total 5 columns):
Date                   573 non-null datetime64[ns]
Cases                  259 non-null float64
Deaths                 259 non-null float64
Interpolated_Cases     573 non-null int32
Interpolated_Deaths    573 non-null int32
dtypes: datetime64[ns](1), float64(2), int32(2)
memory usage: 18.0 KB


In [127]:
# # Plot two charts side by side (Cases and Deaths Over Time)
# fig = make_subplots(rows=1, cols=2, 
#                     subplot_titles=['Confirmed Cases', 'Confirmed Deaths'])

# fig.add_trace(
#     go.Line(x=df_EBOLA['Date'], y=df_EBOLA['Interpolated_Cases'], name='Confirmed Cases', marker_color=yellowGreen),
#     row=1, col=1
# )

# fig.add_trace(
#     go.Line(x=df_EBOLA['Date'], y=df_EBOLA['Interpolated_Deaths'], name='Confirmed Deaths', marker_color=pink),
#     row=1, col=2
# )

# # fig = px.area(df_EBOLA, x='Date', y='Interpolated_Cases', color_discrete_sequence=[green], 
# #               title='Confirmed EBOLA Cases Over Time')

# fig.update_layout(title='Confirmed EBOLA Cases Over Time') # xaxis_tickformat = '%B<br>%Y', xaxis = dict(tickangle = -45)
# fig.show()

# Plot stacked chart (Cases and Deaths Over Time) 
# Unpivot Confirmed, Recovered, Deaths --> Status to display stacked area chart
temp_unpivot = df_EBOLA.melt(id_vars="Date", value_vars=[ 'Interpolated_Deaths','Interpolated_Cases'], var_name='Status', value_name='Count')

fig = px.area(temp_unpivot, x="Date", y="Count", color="Status", height=600,
             title='Stacked EBOLA Cases Over Time',  color_discrete_sequence=[red,blue])
fig.update_layout(xaxis_rangeslider_visible=True)
fig.show()

In [128]:
# df_ebola
df_ebola = df_merged[df_merged['Disease']=='EBOLA']
df_ebola = df_ebola.groupby('Country')['New Cases','New Deaths'].sum().reset_index()

fig = px.choropleth(df_ebola, locations="Country", locationmode="country names", color=np.log(df_ebola["New Cases"]),
                    hover_name="Country", scope='africa',
                    title= 'Confirmed EBOLA Cases in Africa', color_continuous_scale=px.colors.sequential.Greens)

fig.update_geos(countrycolor = "white", landcolor = "rgb(229, 229, 229)", coastlinecolor = "darkgrey")
fig.update_layout(showlegend=False, coloraxis_showscale=False)
fig.show()

#### Cross Disease Analysis

In [129]:
# Get table for SARS to perform cross disease comparison --> need DAYS to put diseases at same scale
df_SARS_sum = df_SARS.groupby('Date')['Interpolated_Cases','Interpolated_Deaths'].sum().reset_index()
df_SARS_sum['Disease'] = 'SARS'
df_SARS_sum['DayOne'] = df_SARS_sum['Date'].min()
df_SARS_sum['Days'] = (df_SARS_sum['Date'] - df_SARS_sum['DayOne']).dt.days

# Get table for H1N1
df_H1N1_sum = df_H1N1.groupby('Date')['Interpolated_Cases','Interpolated_Deaths'].sum().reset_index()
df_H1N1_sum['Disease'] = 'H1N1'
df_H1N1_sum['DayOne'] = df_H1N1_sum['Date'].min()
df_H1N1_sum['Days'] = (df_H1N1_sum['Date'] - df_H1N1_sum['DayOne']).dt.days

# Get table for EBOLA 
df_EBOLA_sum = df_EBOLA.groupby('Date')['Interpolated_Cases','Interpolated_Deaths'].sum().reset_index()
df_EBOLA_sum['Disease'] = 'EBOLA'
df_EBOLA_sum['DayOne'] = df_EBOLA_sum['Date'].min()
df_EBOLA_sum['Days'] = (df_EBOLA_sum['Date'] - df_EBOLA_sum['DayOne']).dt.days

df_concat = pd.concat([df_SARS_sum,df_H1N1_sum,df_EBOLA_sum], axis=0)
df_concat.head()

Date  Interpolated_Cases  Interpolated_Deaths Disease     DayOne  Days
0 2003-03-17                 167                    4    SARS 2003-03-17     0
1 2003-03-18                 219                    4    SARS 2003-03-17     1
2 2003-03-19                 264                    9    SARS 2003-03-17     2
3 2003-03-20                 306                   10    SARS 2003-03-17     3
4 2003-03-21                 350                   10    SARS 2003-03-17     4

In [130]:
# temp_unpivot = df_concat.melt(id_vars=["Disease","Days"], value_vars=['Interpolated_Cases','Interpolated_Deaths'], 
#                               var_name='Status', value_name='Count')

# fig = px.line(temp_unpivot, x='Days', y='Count', facet_col="Status", height=600,
#              color="Disease", color_discrete_sequence=[blue,pink,yellowGreen], title='Confirmed Cases by Disease')

# fig.update_layout(height= 500, shapes=[
#     dict(
#       type= 'line',
#       yref= 'paper', y0= 0, y1= 1,
#       xref= 'x', x0= 49, x1= 49,
#       line=dict(color=lightGrey, width=2,dash="dash")
#     ),
#     dict(
#       type= 'line',
#       yref= 'paper', y0= 0, y1= 1,
#       xref= 'x', x0= 116, x1= 116,
#       line=dict(color=lightGrey, width=2,dash="dash")
#     ),
#     dict(
#       type= 'line',
#       yref= 'paper', y0= 0, y1= 1,
#       xref= 'x', x0= 571, x1= 571,
#       line=dict(color=lightGrey, width=2,dash="dash")
#     )
# ])

# fig.show()